In [108]:
# Import
import pandas as pd
import altair as alt
import numpy as np

In [137]:
# Read data
data = pd.read_csv("../data/raw/amazon_prime_users.csv", sep=";",
                   parse_dates=["Membership Start Date", "Membership End Date", "Date of Birth"], dayfirst=True, index_col=0)

data

Name                   Email Address  \
User ID                                                       
1             Ronald Murphy      williamholland@example.com   
2               Scott Allen             scott22@example.org   
3          Jonathan Parrish            brooke16@example.org   
4            Megan Williams         elizabeth31@example.net   
5             Kathryn Brown  pattersonalexandra@example.org   
...                     ...                             ...   
2546             Pedro Nash              pamela17@welch.com   
2547     Katherine Phillips            benjamin24@gmail.com   
2548            Ashley Ward         toddhenderson@yahoo.com   
2549          Kaylee Watson       oconnellaustin@bryant.org   
2550          Vanessa Silva       williamsphillip@yahoo.com   

                   Username Date of Birth  Gender         Location  \
User ID                                                              
1            williamholland    1953-06-03    Male   Rebeccachester   
2                   scott22    1978-07-08    Male    Mcphersonview   
3                  brooke16    1994-12-06  Female        Youngfort   
4               elizabeth31    1964-12-22  Female     Feliciashire   
5        pattersonalexandra    1961-06-04    Male     Port Deborah   
...                     ...           ...     ...              ...   
2546          jessicamorrow    1984-08-21  Female   Lake Rogerland   
2547            osbornealan    1969-08-31  Female       South Evan   
2548              xphillips    1976-05-27  Female  North Tylerbury   
2549         phillipsjeremy    1990-08-23    Male      Stephenberg   
2550            eatonalison    1964-04-11    Male        Laneville   

        Membership Start Date Membership End Date Subscription Plan  \
User ID                                                               
1                  2024-01-15          2025-01-14            Annual   
2                  2022-01-07          2023-01-06           Monthly   
3                  2022-04-13          2023-04-13           Monthly   
4                  2023-01-24          2024-01-23           Monthly   
5                  2024-02-14          2024-06-13           Monthly   
...                       ...                 ...               ...   
2546               2024-09-12          2025-10-12           Monthly   
2547               2022-08-22          2024-04-10           Monthly   
2548               2023-05-20          2024-01-24           Monthly   
2549               2022-05-17          2026-08-08           Monthly   
2550               2023-10-14          2026-03-30           Monthly   

        Payment Information Renewal Status Usage Frequency Purchase History  \
User ID                                                                       
1                Mastercard         Manual         Regular      Electronics   
2                      Visa         Manual         Regular      Electronics   
3                Mastercard         Manual         Regular            Books   
4                      Amex     Auto-renew         Regular      Electronics   
5                      Visa         Manual        Frequent         Clothing   
...                     ...            ...             ...              ...   
2546                   Amex         Manual      Occasional      Electronics   
2547                   Amex     Auto-renew        Frequent         Clothing   
2548             Mastercard         Manual         Regular           Movies   
2549             Mastercard     Auto-renew      Occasional      Electronics   
2550                   Visa         Manual        Frequent            Music   

        Favorite Genres Devices Used Engagement Metrics  Feedback/Ratings  \
User ID                                                                     
1           Documentary     Smart TV             Medium               3.6   
2                Horror   Smartphone             Medium               3.8   
3                Comedy     Smar

In [141]:
cols = data.columns[np.r_[4, 8:16]]
data[cols] = data[cols].astype('category')

In [142]:
# Check for missing values
data.isna().any().any()

np.False_

In [145]:
# Feature Engineering
data["Age"] = (pd.Timestamp.today() - data["Date of Birth"]).dt.days//365
data["Months Till Expire"] = (
    (data["Membership End Date"] - pd.Timestamp.today()).dt.days//30).clip(lower=0)

In [146]:
# EDA
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2550 entries, 1 to 2550
Data columns (total 20 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   Name                           2550 non-null   object        
 1   Email Address                  2550 non-null   object        
 2   Username                       2550 non-null   object        
 3   Date of Birth                  2550 non-null   datetime64[ns]
 4   Gender                         2550 non-null   category      
 5   Location                       2550 non-null   object        
 6   Membership Start Date          2550 non-null   datetime64[ns]
 7   Membership End Date            2550 non-null   datetime64[ns]
 8   Subscription Plan              2550 non-null   category      
 9   Payment Information            2550 non-null   category      
 10  Renewal Status                 2550 non-null   category      
 11  Usage Frequency       

In [150]:
# Numeric Columns
data.describe(include=["int64", "float64"])

Feedback/Ratings  Customer Support Interactions          Age  \
count       2550.000000                    2550.000000  2550.000000   
mean           3.954196                       4.970588    54.812549   
std            0.648815                       3.190364    21.046012   
min            1.100000                       0.000000    18.000000   
25%            3.500000                       2.000000    36.000000   
50%            4.000000                       5.000000    55.000000   
75%            4.500000                       8.000000    73.000000   
max            5.000000                      10.000000    91.000000   

       Months Till Expire  
count         2550.000000  
mean             0.418824  
std              1.963246  
min              0.000000  
25%              0.000000  
50%              0.000000  
75%              1.000000  
max             32.000000

In [152]:
# Categorical Columns
data.describe(include="category")

Gender Subscription Plan Payment Information Renewal Status  \
count     2550              2550                2550           2550   
unique       2                 2                   3              2   
top     Female            Annual          Mastercard         Manual   
freq      1479              1275                 870           1281   

       Usage Frequency Purchase History Favorite Genres Devices Used  \
count             2550             2550            2550         2550   
unique               3                5               7            4   
top           Frequent            Books          Horror   Smartphone   
freq               874              864             393          881   

       Engagement Metrics  
count                2550  
unique                  3  
top                   Low  
freq                  866

In [210]:
# Age Distribution
alt.Chart(data).mark_bar().encode(
    alt.X(alt.repeat()).bin(),
    alt.Y('count()'),
    color="Gender"
).properties(
    width=300,
    height=200
).facet(
    "Gender"
).repeat(
    ['Feedback/Ratings',
     'Customer Support Interactions', 'Age'],
    columns=1
)

alt.RepeatChart(...)

In [168]:
# Gender Distribution
alt.Chart(data).mark_bar().encode(
    alt.X("Gender"),
    alt.Y('count()'),
).properties(
    width=200,
    height=200
)

alt.Chart(...)

In [205]:
# Categorical
alt.Chart(data).mark_bar().encode(
    alt.X(alt.repeat(), axis=alt.Axis(labelAngle=-30)),
    alt.Y('count()'),
    color="Gender"
).properties(
    width=200,
    height=150
).facet(
    "Gender"
).repeat(
    ['Subscription Plan', 'Payment Information', 'Renewal Status',
     'Usage Frequency', 'Purchase History', 'Favorite Genres',
     'Devices Used', 'Engagement Metrics'],
    columns=1
)

alt.RepeatChart(...)